Let us import all necessary modules:

In [ ]:
import csv
import math
import matplotlib.pyplot as plt
import numpy as np
import random
from scipy import spatial
from sko.GA import GA_TSP
import sys

Some of the algorithms allow for a visualization of the intermediate steps. With this variable we can swtich it on or off.

In [ ]:
showProgress=False

We initialize a certain number of Monte Carlo rounds.

In [ ]:
rounds=10

We take as distance the euclidean distance between two points. However, you can experiment with other metrics, e.g., the Manhatten distance.

In [ ]:
def Distance(p,q):
  """Returns distance between points p and q assuming that the x- and
  y-coordinates are the first and second entry of the point-tuple"""
  #return math.fabs(p[0]-q[0])+math.fabs(p[1]-q[1])
  return math.hypot(p[0]-q[0],p[1]-q[1])

A helper function that just computes the side lengths of the triangle built by the three given points.

In [ ]:
def TriangleSides(prev,curr,p):
  s0=Distance(prev,curr)
  s1=Distance(prev,p)
  s2=Distance(p,curr)
  return s0,s1,s2

We read a tour in TSPLIB format. Observe that we assume `csv`-files where the separator is the blank, so maybe you need to modify the original files from TSPLIB and remove all spaces in front of a colon etc.

This function tries to read the corresponding optimal tour as well, whenever available in the same directory.

In [ ]:
def ReadTsp(fn):
  f=open(fn+".tsp","rt")
  reader=csv.reader(f,delimiter=" ",skipinitialspace=True)
  coordinates=False
  cities=[]
  best=0.0
  index=0
  for row in reader:
    if row[0]=="EOF":
      break
    elif coordinates:
      cities.append((float(row[1]),float(row[2]),index))
      index+=1
    elif row[0]=="BEST:":
      best=float(row[1])
    elif row[0]=="NAME:":
      print("reading tour",row[1])
    elif row[0]=="NODE_COORD_SECTION":
      coordinates=True
  f.close()
  opt=[]
  try:
    f=open(fn+".opt.tour","rt")
    reader=csv.reader(f,delimiter=" ",skipinitialspace=True)
    coordinates=False
    for row in reader:
      if row[0]=="EOF" or row[0]=="-1":
        break
      elif coordinates:
        index=int(row[0])
        opt.append((cities[index-1][0],cities[index-1][1],index))
      elif row[0]=="NAME:":
        print("reading optimal tour",row[1])
      elif row[0]=="TOUR_SECTION":
        coordinates=True
  except FileNotFoundError:
    print("optimal tour not available")
  finally:
    f.close()

  print("reading done",best)
  return cities,best,opt

Given a filename and a tour, we write a tour in TSPLIB optimal tour format.

In [ ]:
def WriteTsp(fn,T):
  f=open(fn+".opt.tour","wt")
  f.write("NAME: "+fn+".opt.tour\n")
  f.write("COMMENT : Length "+str(TourLength(T))+"\n")
  f.write("COMMENT : Found by tsp [Arno Formella]\n")
  f.write("TYPE: TOUR\n")
  f.write("DIMENSION: "+str(len(T))+"\n")
  f.write("TOUR_SECTION\n")
  for t in T:
    f.write(str(t[2]+1)+"\n")
  f.write("-1\n")
  f.write("EOF\n")
  f.close()
  print("writing done")

We compute the length of a tour by accumulating all distances between neighbors.

In [ ]:
def TourLength(T):
  t=len(T)
  prev=T[t-1]
  length=0.0
  for i in range(0,t):
    curr=T[i]
    length+=Distance(prev,curr)
    prev=curr
  return length

As error we use the relative error of the current length compared to the length of the optimal tour in percent.

In [ ]:
def TourError(T,best_length):
  return 100.0*(TourLength(T)-best_length)/best_length

We want to plot a tour in a certain color and with/without the connecting segments. Whenever a filename is given, we write a corresponding `.png`-image as output.

In [ ]:
def PlotTour(T,col,show=False,onlypoints=False,fn=None):
  if T!=[]:
    T.append(T[0])
    x,y,i = zip(*T)
    T.pop(-1)
    fig,ax=plt.subplots(figsize=(12.8,9.6))
    for label in (ax.get_xticklabels()+ax.get_yticklabels()):
      label.set_fontsize(16)

    if onlypoints==True:
      ax.scatter(
        x,y,s=100,color=col,marker="o",linewidth=3
      )
    else:
      ax.plot(
        x,y,color=col,marker="o",linewidth=3,markeredgewidth=3,markersize=10
      )
  if fn!=None:
    plt.savefig(fn,transparent=True,bbox_inches='tight')
  if show==True:
    plt.show()

In order to plot a partial tour (to be able to animate the algorithms) we plot such a tour on top of all cities in a similar way as plotting a complete tour.

In [ ]:
def PlotProgressTour(C,T,col,show=False,onlypoints=False,fn=None):
  if not showProgress:
    return
  fig,ax=plt.subplots(figsize=(12.8,9.6))
  for label in (ax.get_xticklabels()+ax.get_yticklabels()):
    label.set_fontsize(16)
  x,y,i = zip(*C)
  ax.scatter(
    x,y,s=100,color=col,marker="o",linewidth=3
  )
  offset=0
  if T!=[]:
    T.append(T[0])
    x,y,i = zip(*T)
    T.pop(-1)
    if onlypoints==True:
      ax.scatter(
        x,y,s=100,color="cyan",marker="o",linewidth=3
      )
      offset=len(C)
    else:
      ax.plot(
        x,y,color="cyan",marker="o",linewidth=3,markeredgewidth=3,markersize=10
      )
  if fn!=None:
    plt.savefig(fn+"%03d"%(len(T)+offset),transparent=True,bbox_inches='tight')
  if show==True:
    plt.show()

### The quick tour approach

  idea:
  - generate a random permutation of the cities
  - take the first three cities to form a triangle to start with
  - proceed with the rest of the points in given random order
    and insert a new city such that the tour increase is minimal
    among all possible insertions
  - stop when there is no more city
  
First we implement the function that returns the index within the given tour T where an insertion of the point p results in a minimum increase of the overall tour length.


In [ ]:
def BestInsertionIndex(T,p):
  
  t=len(T)
  prev=T[t-1]
  curr=T[0]
  s0,s1,s2=TriangleSides(prev,curr,p)
  best_i,shortest=0,s1+s2-s0
  prev=curr
  for i in range(1,t):
    curr=T[i]
    s0,s1,s2=TriangleSides(prev,curr,p)
    increase=s1+s2-s0
    if increase<shortest:
      best_i,shortest=i,increase
    prev=curr
  # print("shortest",shortest,"at",best_i)
  return best_i

Now we implement the overall quick tour algorithm embedded into a Monte Carlo loop with a certain number of rounds and a Las Vegas condition, so we can stop when we found an optimal tour.

We keep and return the best tour that we found during the Monte Carlo loop.

In [ ]:
def QuickTour(Cities,rounds,best_length):
  min_error=sys.float_info.max
  best_tour=[]
  for j in range(0,rounds): # the Monte Carlo loop
    cities=Cities.copy()       # take a new copy of the cities
    random.shuffle(cities)     # mix them up
    tour=[]
    tour.append(cities.pop(0)) # take the first three as starting triangle
    tour.append(cities.pop(0))
    tour.append(cities.pop(0))

    while cities!=[]:  # while there are still unconnected cities
      PlotProgressTour(
        Cities,tour,"skyblue",show=True,onlypoints=False,fn="progress_QT"
      )
      c=cities.pop(0)  # take the next city
      i=BestInsertionIndex(tour,c)  # get tour segment with smallest increase
      tour.insert(i,c) # insert city replacing the segment by two new ones
    PlotProgressTour(
      Cities,tour,"skyblue",show=True,onlypoints=False,fn="progress_QT"
    )

    error=TourError(tour,best_length)
    print(j+1,"relative error quick tour: ",error,"%")
    if error<min_error:
      min_error=error
      best_tour=tour.copy()
    if error==0.0: # the Las Vegas condition
      print("optimum found in",j,"rounds")
      WriteTsp("bestTour",best_tour)
      break
  return best_tour,min_error

Let us run the quick tour algorithm on some example.

In [ ]:
filename='berlin52'
theCities,bestLength,bestTour=ReadTsp(filename)
if bestLength!=TourLength(bestTour):
  print("strange best tour given",TourLength(bestTour))

bestT,error=QuickTour(theCities,rounds,bestLength)
print("relative error quick tour ",error,"%")
PlotTour(bestT,"skyblue",show=True,fn=filename+"_QuickTour.png")

###  the classical closest-neighbor approach
  idea:
  - select a random city
  - proceed with connecting the closest still unconnected city
  - stop when there is no more city
  
We implement the algorithm embedded into a Monte Carlo loop with a certain number of rounds and a Las Vegas condition so we can stop when we found an optimal tour.

We keep and return the best tour that we found during the Monte Carlo loop.

In [ ]:
def ClosestNeighborTour(Cities,rounds,best_length):
  min_error=sys.float_info.max
  best_tour=[]
  # because we have random tie break, more rounds than there are points
  # can be advantageous
  for j in range(0,rounds): # the Monte Carlo loop
    cities=Cities.copy()
    random.shuffle(cities)
    tour=[]
    tour.append(cities.pop(0))
    while cities!=[]:
      min_dis=sys.float_info.max
      p=tour[0][0],tour[0][1]
      candidates=[]
      for i in range(0,len(cities)):
        q=cities[i][0],cities[i][1]
        dis=Distance(p,q)
        if dis<min_dis:
          min_dis=dis
          candidates=[]
          candidates.append(i)
        elif dis==min_dis:
          candidates.append(i)
      tour.insert(0,cities.pop(candidates[random.randrange(len(candidates))]))
      PlotProgressTour(Cities,tour,"red",show=True,fn="progress_CN")

    error=TourError(tour,best_length)
    print(j+1,"relative error closest neighbor: ",error,"%")
    if error<min_error:
      min_error=error
      best_tour=tour.copy()
    if error==0.0: # the Las Vegas condition
      print("optimum found in",j,"rounds")
      break
  return best_tour,min_error

Let us run the closest neighbor tour algorithm on some example.

In [ ]:
filename='berlin52'
theCities,bestLength,bestTour=ReadTsp(filename)
if bestLength!=TourLength(bestTour):
  print("strange best tour given",TourLength(bestTour))

bestT,error=ClosestNeighborTour(theCities,rounds,bestLength)
print("relative error closest-neighbor tour: ",error,"%")
PlotTour(bestT,"red",show=True,fn=filename+"_ClosestNeighbor.png")

### The pair-center tour approach
  idea:
  - find closest pair among all pairs of cities
  - substitute this pair of cities by a center city
  - proceed until there is only one city left
  - now we have a binary tree structure
  - travel through the tree top-down and replace
    a "center" by its underlying pair taking care of inserting
    the best possibility
  - stop when all pairs are handled
  
The algorithm uses a data structure of a dictionary to hold the binary tree. Each entry in the dictionary uses as key the index of the current point (either an orignal city or a center being constructed during the progress of the algorithm) and as information a tuple that holds both indices of the points being paired and the coordinates. Hence the tuple `(i,j,x,y)` is the center of points with index `i` and index `j` at location `(x,y)`.

 We need a function that returns a pair of indices with minimal distance among all possible
 distances witin the point set L.
 If there is more than one such pair, a random one of those is returned.

In [ ]:
def ClosestPair(L):
  t=len(L)
  best=sys.float_info.max
  pairs=[]
  for i in range(0,t):
    for j in range(i+1,t):
      s0=Distance(L[i],L[j])
      if s0<best:
        best=s0
        pairs=[]
        pairs.append((i,j))
      elif s0==best:
        pairs.append((i,j))
  return pairs[random.randrange(len(pairs))]

Given a list of indices (keys) into a dictionary we build the corresponding tour.

In [ ]:
def MakeTourWithDictionary(I,D):
  T=[]
  for i in I:
    T.append((D[i][2],D[i][3],i))
  return T

Now we implement the overall pair-center tour algorithm which is a deterministic heuristic algorithm. this version is still not optimal, it could be improved by handling the closest pairs in a more sophisticated data structure, so the overall runtime can be brought down from cubic to quadratic. 

In [ ]:
def PairCenterTour(Cities,best_length):
  cities=Cities.copy()
  mark=0
  D={}
  for p in Cities:
    D[mark]=(-1,-1,p[0],p[1])
    mark+=1

  # Deterministic algorithm with pair-center connections
  # First build the binary tree inserting the corresponding centers
  while len(cities)>1:
    a,b=ClosestPair(cities);
    x,y=0.5*(cities[a][0]+cities[b][0]),0.5*(cities[a][1]+cities[b][1])
    D[mark]=(cities[a][2],cities[b][2],x,y)
    cities[a]=(x,y,mark)
    mark+=1
    cities.pop(b)
    PlotProgressTour(
      Cities,cities,"blue",show=True,onlypoints=True,fn="progress_PC"
    )

  # Run the tree downwards and insert the corresponding pair in
  # the best possible way
  mark-=1
  L=[]
  L.append(D[mark][0])
  PlotProgressTour(
    Cities,MakeTourWithDictionary(L,D),"blue",show=True,
    onlypoints=False,fn="progress_PC"
  )
  L.append(D[mark][1])
  PlotProgressTour(
    Cities,MakeTourWithDictionary(L,D),"blue",show=True,
    onlypoints=False,fn="progress_PC"
  )
  t=len(Cities)
  for m in range(mark-1,t-1,-1):
    i=L.index(m)
    Di0=D[L[i]][0]
    Di1=D[L[i]][1]
    q=(D[Di0][2],D[Di0][3])
    r=(D[Di1][2],D[Di1][3])
    p=s=(0,0)
    if i==len(L)-1:
      p=(D[L[i-1]][2],D[L[i-1]][3])
      s=(D[L[0]][2],D[L[0]][3])
    elif i==0:
      p=(D[L[len(L)-1]][2],D[L[len(L)-1]][3])
      s=(D[L[1]][2],D[L[1]][3])
    else:
      p=(D[L[i-1]][2],D[L[i-1]][3])
      s=(D[L[i+1]][2],D[L[i+1]][3])

    if Distance(p,q)+Distance(r,s)>Distance(p,r)+Distance(q,s):
      L[i]=D[m][1]
      L.insert(i+1,D[m][0])
    else:
      L[i]=D[m][0]
      L.insert(i+1,D[m][1])
    PlotProgressTour(
      Cities,MakeTourWithDictionary(L,D),"blue",show=True,
      onlypoints=False,fn="progress_PC"
    )

  tour=MakeTourWithDictionary(L,D)
  error=TourError(tour,best_length)
  return tour,error

Let's run the pair-center algorithm on some example:

In [ ]:
filename='berlin52'
theCities,bestLength,bestTour=ReadTsp(filename)
if bestLength!=TourLength(bestTour):
  print("strange best tour given",TourLength(bestTour))

bestT,error=PairCenterTour(theCities,bestLength)
print("relative error pair-center tour: ",error,"%")
PlotTour(bestT,"blue",show=True,fn=filename+"_PairCenter.png")

Given a list of indices into the list of location, we build the corresponding tour.

In [ ]:
def MakeTourWithCities(I,C):
  T=[]
  for i in I:
    T.append((C[i][0],C[i][1],i))
  return T

We implement the computation of a tour with the genetic algorithm from the `scikit-opt` package.

In [ ]:
def GeneticAlgorithmTour(cities,best_length):
  n=len(cities)
  points_coordinate=[(l[0],l[1]) for l in cities]

  dist_mat=spatial.distance.cdist(
    points_coordinate, points_coordinate, metric='euclidean'
  )

  def cal_total_distance(routine):
      '''The objective function. input routine, return total distance.
      cal_total_distance(np.arange(n))
      '''
      n, = routine.shape
      return sum([dist_mat[routine[i%n], routine[(i+1)%n]] for i in range(n)])

  ga_tsp=GA_TSP(
    func=cal_total_distance, n_dim=n, size_pop=50, max_iter=1000, prob_mut=1
  )
  best_points, best_distance = ga_tsp.run()
  T=MakeTourWithCities(best_points,theCities)
  error=TourError(T,bestLength)
  return T,error

In [ ]:
filename='berlin52'
theCities,bestLength,bestTour=ReadTsp(filename)
if bestLength!=TourLength(bestTour):
  print("strange best tour given",TourLength(bestTour))

bestT,error=GeneticAlgorithmTour(theCities,bestLength)
print("relative error genetic algorithm: ",error,"%")
PlotTour(bestT,"green",show=True,fn=filename+"_GeneticAlgorithm.png")

We read an example dataset and calculate the complete matrix of interpoint distances and compute the simple lower bound for the length of a tour. We plot both: the cities and the best tour from the input file.

In [ ]:
def LowerBound(M,n):
  if len(M)!=n*n:
    print("usage error in LowerBound")
    exit()
  lower=0.0
  for i in range(0,n):
    min_index=sys.float_info.max
    for j in range(0,n):
      if i!=j:
        curr=M[i*nloc+j]
        if curr<min_index:
          min_index=curr
    lower+=min_index
  return lower

In [ ]:
filename='berlin52'
theCities,bestLength,bestTour=ReadTsp(filename)
if bestLength!=TourLength(bestTour):
  print("strange best tour given",TourLength(bestTour))

nloc=len(theCities)
Dmat = [
  Distance((theCities[i][0],theCities[i][1]),(theCities[j][0],theCities[j][1]))
    for i in range(0,nloc) for j in range(0,nloc)
  ]
print("lower bound",LowerBound(Dmat,nloc))
PlotTour(theCities,"magenta",show=True,onlypoints=True,fn=filename+"_Cities.png")

# show best tour
print("best tour length",bestLength)
PlotTour(bestTour,"magenta",show=True,fn=filename+"_BestTour")